<a href="https://colab.research.google.com/github/mitsukacke2285/drug_discovery_repo/blob/main/Docking_with_gnina.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Set Up
The cells in this section set up the software and files we will need for our calculations.
Gnina will run within a linux environment provided by google colab virtual machine.




### Install Python Packages  
1. `useful_rdkit_utils` is a Python package written and maintained by Pat Walters that contains useful RDKit functions. We will use it for the functions `mcs_rmsd` (explained later).
2. `py3Dmol` is used for molecular visualization.
3. The RDKit is a popular cheminiformatics package we will use for processing molecules.


In [8]:
%%capture
!pip install useful_rdkit_utils py3Dmol rdkit # If this command doesn't work, run each command separately
!apt install openbabel

In [2]:
!pip install py3Dmol

In [9]:
!pip install rdkit

In [10]:
!pip install useful_rdkit_utils

In [5]:
!curl -L -O https://raw.githubusercontent.com/MolSSI-Education/iqb-2025/main/util.py

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  2927  100  2927    0     0  16906      0 --:--:-- --:--:-- --:--:-- 16919


### Download gnina

We are downloading the pre-compiled binary of gnina. You may also compile gnina yourself by following the directions on the [gnina GitHub repository](https://github.com/gnina/gnina).

In [11]:
# Download gnina
!wget https://github.com/gnina/gnina/releases/download/v1.3/gnina.fix

--2025-10-16 10:17:22--  https://github.com/gnina/gnina/releases/download/v1.3/gnina.fix
Resolving github.com (github.com)... 140.82.114.3
Connecting to github.com (github.com)|140.82.114.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://release-assets.githubusercontent.com/github-production-release-asset/45548146/a7090e9d-ca5b-4232-b307-e29a70dbe6d5?sp=r&sv=2018-11-09&sr=b&spr=https&se=2025-10-16T11%3A10%3A38Z&rscd=attachment%3B+filename%3Dgnina.fix&rsct=application%2Foctet-stream&skoid=96c2d410-5711-43a1-aedd-ab1947aa7ab0&sktid=398a6654-997b-47e9-b12b-9515b896b4de&skt=2025-10-16T10%3A10%3A16Z&ske=2025-10-16T11%3A10%3A38Z&sks=b&skv=2018-11-09&sig=E%2BVbYU7kDVEUQBnil6TtFDnjLXsc6nriCEgWxG320%2BY%3D&jwt=eyJ0eXAiOiJKV1QiLCJhbGciOiJIUzI1NiJ9.eyJpc3MiOiJnaXRodWIuY29tIiwiYXVkIjoicmVsZWFzZS1hc3NldHMuZ2l0aHVidXNlcmNvbnRlbnQuY29tIiwia2V5Ijoia2V5MSIsImV4cCI6MTc2MDYxMzQ0MiwibmJmIjoxNzYwNjA5ODQyLCJwYXRoIjoicmVsZWFzZWFzc2V0cHJvZHVjdGlvbi5ibG9iLmNvcmUud2luZG93c

In [12]:
# Make gnina executable
!mv gnina.fix gnina
!chmod +x gnina

### Get Lesson Files

We have stored the files created in the last notebook as a zip file and stored it on GitHub. This cell downloads that file as well as `util.py` which contains a custom utility function for visualizing our ligand and protein.



In [40]:
#%%capture
!wget https://github.com/MolSSI-Education/iqb-2025/raw/refs/heads/main/data/docking_files.zip
!wget https://raw.githubusercontent.com/MolSSI-Education/iqb-2025/refs/heads/main/util.py

--2025-10-16 11:03:14--  https://github.com/MolSSI-Education/iqb-2025/raw/refs/heads/main/data/docking_files.zip
Resolving github.com (github.com)... 140.82.114.4
Connecting to github.com (github.com)|140.82.114.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/MolSSI-Education/iqb-2025/refs/heads/main/data/docking_files.zip [following]
--2025-10-16 11:03:14--  https://raw.githubusercontent.com/MolSSI-Education/iqb-2025/refs/heads/main/data/docking_files.zip
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1090053 (1.0M) [application/zip]
Saving to: ‘docking_files.zip’

docking_files.zip   100%[===================>]   1.04M  --.-KB/s    in 0.05s   

2025-10-16 11:03:15 (21.5 MB/s) - ‘docking_fil

In [41]:
!unzip docking_files.zip

Archive:  docking_files.zip
   creating: docking_files/
   creating: docking_files/protein_structures/
  inflating: docking_files/protein_structures/7L11_aligned_fixed.pdb  
  inflating: docking_files/protein_structures/7L11_aligned.pdb  
  inflating: docking_files/protein_structures/7LME_fixed.pdb  
  inflating: docking_files/protein_structures/7LME.pdb  
  inflating: docking_files/protein_structures/7L11.pdb  
  inflating: docking_files/protein_structures/7LME.pdbqt  
  inflating: docking_files/protein_structures/7L11.pdbqt  
   creating: docking_files/ligand_structures/
  inflating: docking_files/ligand_structures/Y6J_ideal.sdf  
  inflating: docking_files/ligand_structures/XF1_ideal.sdf  
  inflating: docking_files/ligand_structures/ligands_to_dock.sdf  
  inflating: docking_files/ligand_structures/Y6J_corrected_pose.sdf  
  inflating: docking_files/ligand_structures/XF1_corrected_pose.sdf  
  inflating: docking_files/ligand_structures/Y6J_fromPDB.pdb  
  inflating: docking_files/l

In [20]:
from google.colab import files

# Upload {pdb_id}_A.pdbqt {pdb_id}_A_fixed.pdb files from local PC to your Colab VM
files.upload("molecular_docking/protein_files")

# Download a file from your Colab VM to local PC
#files.download('mylocalfile.txt')

Saving 7LME_A.pdb to molecular_docking/protein_files/7LME_A.pdb


{'molecular_docking/protein_files/7LME_A.pdb': b'ATOM      1  N   SER A   1     -10.713   4.700  34.877  1.00 32.67           N  \r\nATOM      2  CA  SER A   1     -10.217   5.615  33.865  1.00 31.77           C  \r\nATOM      3  C   SER A   1      -8.686   5.749  33.911  1.00 34.67           C  \r\nATOM      4  O   SER A   1      -7.979   4.805  34.287  1.00 28.09           O  \r\nATOM      5  CB  SER A   1     -10.877   6.989  34.024  1.00 38.94           C  \r\nATOM      6  OG  SER A   1     -10.602   7.555  35.293  1.00 41.88           O  \r\nATOM      7  N   GLY A   2      -8.187   6.922  33.530  1.00 29.30           N  \r\nATOM      8  CA  GLY A   2      -6.773   7.122  33.287  1.00 28.61           C  \r\nATOM      9  C   GLY A   2      -6.384   6.800  31.849  1.00 29.15           C  \r\nATOM     10  O   GLY A   2      -7.082   6.096  31.121  1.00 31.32           O  \r\nATOM     11  N   PHE A   3      -5.238   7.333  31.435  1.00 28.28           N  \r\nATOM     12  CA  PHE A   3 

In [16]:
# Upload {ligand_id}_ideal.sdf, {ligand_id}_corrected_pose.sdf  ligands_to_dock.sdf from local machine to google colab VM
files.upload("molecular_docking/ligand_structures")

Saving Y6J_corrected_pose.sdf to molecular_docking/ligand_structures/Y6J_corrected_pose.sdf


{'molecular_docking/ligand_structures/Y6J_corrected_pose.sdf': b'\r\n     RDKit          3D\r\n\r\n 52 56  0  0  0  0  0  0  0  0999 V2000\r\n   22.1100    1.1250   18.6290 C   0  0  0  0  0  0  0  0  0  0  0  0\r\n   21.1230    0.6020   17.8220 N   0  0  0  0  0  0  0  0  0  0  0  0\r\n   25.5760    0.1650   14.0050 N   0  0  0  0  0  0  0  0  0  0  0  0\r\n   25.1860    0.6510   11.6850 C   0  0  0  0  0  0  0  0  0  0  0  0\r\n   26.2970   -1.1030   14.2330 C   0  0  0  0  0  0  0  0  0  0  0  0\r\n   27.6520   -3.4870   14.6740 C   0  0  0  0  0  0  0  0  0  0  0  0\r\n   24.9460    1.4720   10.4180 C   0  0  0  0  0  0  0  0  0  0  0  0\r\n   24.1250    0.6970    9.5180 C   0  0  0  0  0  0  0  0  0  0  0  0\r\n   24.5110   -0.6160   11.5710 C   0  0  0  0  0  0  0  0  0  0  0  0\r\n   24.4180    0.4830   14.8670 C   0  0  0  0  0  0  0  0  0  0  0  0\r\n   24.0160   -0.5260   15.9810 C   0  0  0  0  0  0  0  0  0  0  0  0\r\n   23.3280    0.7660   18.0420 C   0  0  0  0  0  0  0 

## Set protein and ligand directory

In [18]:
import os
import requests

pdb_id = input("Enter PDB code: ") # The Protein ID we're looking at
ligand_id = input("Enter ligand code: ") # The ligand ID we're looking at

# Start by making a directory for us to work in and stage our intermediate files
protein_directory = "molecular_docking/protein_files"
protein_filename = f"{pdb_id}.pdb"
ligand_directory = "molecular_docking/ligand_structures"
ideal_ligand_filename = f"{ligand_id}_ideal.sdf"
docking_results_directory = "molecular_docking/docking_results"


Enter PDB code: 7LME
Enter ligand code: Y6J


## Redocking the Ligand

Redocking (also called "cognate docking") involves redocking a ligand back into the receptor structure from which the bound pose was experimentally determined.
Redocking is typically done to evaluate how well a docking program's sampling algorithm and scoring function and reproduce a known experimental binding pose.

We will begin our docking journey with gnina by performing a redock of our ligand.

In [23]:
from util import visualize_poses

v = visualize_poses(
    f"{protein_directory}/{pdb_id}_A_fixed.pdb",
    f"{ligand_directory}/{ligand_id}_ideal.sdf",
    animate=False
)
v.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

You may execute the cell below, and read the following explanation on the input parameters for gnina. gnina works through the command line, so we cannot use in-line comments.

```
./gnina \
  # Specify the receptor structure file (-r).
  # This file (7LME.pdbqt) should be prepared for docking (e.g., with hydrogens added).
  -r docking_files/7LME_all_atom.pdbqt \
  # Specify the ligand structure file (-l) to be docked.
  # This file (Y6J_ideal.pdbqt) contains the 3D coordinates of the ligand.
  -l docking_files/Y6J_ideal.pdbqt \
  # Define the docking search box automatically (--autobox_ligand).
  # The box will be centered around the coordinates of the ligand in the specified file
  # (Y6J_corrected_pose.sdf), which is the known experimental pose in this redocking example.
  # An optional padding (default 4Å) is added.
  --autobox_ligand docking_files/Y6J_corrected_pose.sdf \
  # Specify the output file path (-o) where the resulting docked poses will be saved.
  # The output format will be SDF, containing multiple poses ranked by score.
  -o docking_results/Y6J_docked_e12.sdf \
  # Set the random number generator seed (--seed) to 0.
  # Using a fixed seed makes the docking calculation reproducible.
  --seed 0 \
  # Set the exhaustiveness level (--exhaustiveness) to 12.
  # This controls the number of Monte Carlo chains for the ligand.
  # The default is 8
  --exhaustiveness 16
  ```

  Execute the next cell to run gnina.


In [38]:
# Run gnina
!mkdir molecular_docking/docking_results

cmd = f"""./gnina \
  -r {protein_directory}/{pdb_id}_A.pdbqt \
  -l {ligand_directory}/{ligand_id}_ideal.sdf \
  --autobox_ligand {ligand_directory}/{ligand_id}_corrected_pose.sdf \
  -o {docking_results_directory}/{ligand_id}_docked_{pdb_id}.sdf \
  --seed 0 \
  --exhaustiveness 16"""

!{cmd}

              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:25e64da   Built Apr 23 2025.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Recommend running with single model (--cnn fast)
or without cnn scoring (--cnn_scoring=none).

Commandline: ./gnina -r molecular_docking/protein_files/7LME_A.pdbqt -l molecular_docking/ligand_structures/Y6J_ideal.sdf --autobox_ligand molecular_docking/ligand_structures/Y6J_corrected_pose.sdf -o molecular_docking/docking_results/Y6J_docked_7LME.sdf --seed 0 --exhaustiveness 16
Using random seed: 0

0%   10   20   30   40   50   60   70   80   90   100%
|----|----|----|----|----|----|----|----|----|----|
***************************************************
Y6J | pose 0 | initial pose not within box

mode |  affinity  |  intramol  |    CNN     |   C

In [44]:
# Run gnina
!mkdir docking_results

!./gnina \
  -r docking_files/protein_structures/7LME.pdbqt \
  -l docking_files/ligand_structures/Y6J_ideal.sdf \
  --autobox_ligand docking_files/ligand_structures/Y6J_corrected_pose.sdf \
  -o docking_results/Y6J_docked_7LME.sdf \
  --seed 0 \
  --exhaustiveness 16

              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:25e64da   Built Apr 23 2025.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Recommend running with single model (--cnn fast)
or without cnn scoring (--cnn_scoring=none).

Commandline: ./gnina -r docking_files/protein_structures/7LME.pdbqt -l docking_files/ligand_structures/Y6J_ideal.sdf --autobox_ligand docking_files/ligand_structures/Y6J_corrected_pose.sdf -o docking_results/Y6J_docked_7LME.sdf --seed 0 --exhaustiveness 16
Using random seed: 0

0%   10   20   30   40   50   60   70   80   90   100%
|----|----|----|----|----|----|----|----|----|----|
***************************************************
Y6J | pose 0 | initial pose not within box

mode |  affinity  |  intramol  |    CNN     |   CNN
     | (kcal/mol) | (kca

In [ ]:
# Docking without CNN
!./gnina \
  -r docking_files/protein_structures/7LME.pdbqt \
  -l docking_files/ligand_structures/Y6J_ideal.sdf \
  --autobox_ligand docking_files/ligand_structures/Y6J_corrected_pose.sdf \
  -o docking_results/Y6J_docked_7LME.sdf \
  --cnn_scoring none \
  --seed 0 \
  --exhaustiveness 16

### Visualizing the Docked Structures

In the cell below, we use a function called `visualize_docked_structures`, a custom function defined for this workshop that we obtained above when we retreived `util.py`.
This function allows us to view our generated docked structures along with ligand it its original experimentally determined position.

In [47]:
v = visualize_poses(
    f"{protein_directory}/{pdb_id}_A_fixed.pdb",
    f"{docking_results_directory}/{ligand_id}_docked_{pdb_id}.sdf",
    cognate_file=f"{ligand_directory}/{ligand_id}_corrected_pose.sdf",
    animate=False,
)  # Change to True to see an animation of all of the poses
v.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [45]:
v = visualize_poses(
    "docking_files/protein_structures/7LME_fixed.pdb",
    "docking_files/ligand_structures/Y6J_ideal.sdf",
    cognate_file="docking_files/ligand_structures/Y6J_corrected_pose.sdf",
    animate=False,
)  # Change to True to see an animation of all of the poses
v.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

**RMSD Analysis**

In [42]:
import useful_rdkit_utils as uru
from rdkit import Chem

cognate = Chem.MolFromMolFile(f"{ligand_directory}/{ligand_id}_corrected_pose.sdf")
poses = Chem.SDMolSupplier(f"{docking_results_directory}/{ligand_id}_docked_{pdb_id}.sdf")

for i, pose in enumerate(poses):
    n_match, rmsd = uru.mcs_rmsd(cognate, pose)
    print(f"{n_match}\t{rmsd:.2f}")

31	8.06
31	2.79
31	6.17
31	8.73
31	8.50
31	8.25
31	5.52
31	6.60
31	8.18


[11:05:00] Warning: molecule is tagged as 2D, but at least one Z coordinate is not zero. Marking the mol as 3D.
[11:05:00] Warning: molecule is tagged as 2D, but at least one Z coordinate is not zero. Marking the mol as 3D.
[11:05:00] Warning: molecule is tagged as 2D, but at least one Z coordinate is not zero. Marking the mol as 3D.
[11:05:00] Warning: molecule is tagged as 2D, but at least one Z coordinate is not zero. Marking the mol as 3D.
[11:05:00] Warning: molecule is tagged as 2D, but at least one Z coordinate is not zero. Marking the mol as 3D.
[11:05:00] Warning: molecule is tagged as 2D, but at least one Z coordinate is not zero. Marking the mol as 3D.
[11:05:00] Warning: molecule is tagged as 2D, but at least one Z coordinate is not zero. Marking the mol as 3D.
[11:05:00] Warning: molecule is tagged as 2D, but at least one Z coordinate is not zero. Marking the mol as 3D.
[11:05:00] Warning: molecule is tagged as 2D, but at least one Z coordinate is not zero. Marking the mol

## Docking our Prepared Ligands

In this section, we will dock the ligands we prepared in our previous notebook. Luckily, gnina allows docking of multiple ligands by providing an SDF with your ligands of choice.

In [ ]:
!./gnina \
  -r docking_files/protein_structures/7LME.pdbqt \
  -l docking_files/ligand_structures/ligands_to_dock.sdf \
  --autobox_ligand docking_files/ligand_structures/Y6J_corrected_pose.sdf \
  -o docking_results/multiple_ligands_docked.sdf \
  --cnn_scoring none \
  --seed 0 \
  --exhaustiveness 16

              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:25e64da   Built Apr 23 2025.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Recommend running with single model (--cnn fast)
or without cnn scoring (--cnn_scoring=none).

Commandline: ./gnina -r docking_files/protein_structures/7LME.pdbqt -l docking_files/ligand_structures/ligands_to_dock.sdf --autobox_ligand docking_files/ligand_structures/Y6J_corrected_pose.sdf -o docking_results/multiple_ligands_docked.sdf --cnn_scoring none --seed 0 --exhaustiveness 16
Using random seed: 0

0%   10   20   30   40   50   60   70   80   90   100%
|----|----|----|----|----|----|----|----|----|----|
***************************************************
Compound_12_i0 | pose 0 | initial pose not within box

mode |  affinity  |  intramol  |

In [49]:
# Run gnina
!mkdir molecular_docking/docking_results

cmd = f"""./gnina \
  -r {protein_directory}/{pdb_id}_A.pdbqt \
  -l {ligand_directory}/"ligands_to_dock.sdf" \
  --autobox_ligand {ligand_directory}/{ligand_id}_corrected_pose.sdf \
  -o {docking_results_directory}/{ligand_id}_docked_{pdb_id}.sdf \
  --seed 0 \
  --exhaustiveness 16"""

!{cmd}

mkdir: cannot create directory ‘molecular_docking/docking_results’: File exists
              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:25e64da   Built Apr 23 2025.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Recommend running with single model (--cnn fast)
or without cnn scoring (--cnn_scoring=none).

Commandline: ./gnina -r molecular_docking/protein_files/7LME_A.pdbqt -l molecular_docking/ligand_structures/ligands_to_dock.sdf --autobox_ligand molecular_docking/ligand_structures/Y6J_corrected_pose.sdf -o molecular_docking/docking_results/Y6J_docked_7LME.sdf --seed 0 --exhaustiveness 16
Using random seed: 0

0%   10   20   30   40   50   60   70   80   90   100%
|----|----|----|----|----|----|----|----|----|----|
***************************************************
_i0 | p

In [ ]:
!wget https://github.com/MolSSI-Education/iqb-2025/raw/refs/heads/main/data/docking_results.zip
!unzip -o docking_results.zip

--2025-10-15 08:16:56--  https://github.com/MolSSI-Education/iqb-2025/raw/refs/heads/main/data/docking_results.zip
Resolving github.com (github.com)... 140.82.112.4
Connecting to github.com (github.com)|140.82.112.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/MolSSI-Education/iqb-2025/refs/heads/main/data/docking_results.zip [following]
--2025-10-15 08:16:56--  https://raw.githubusercontent.com/MolSSI-Education/iqb-2025/refs/heads/main/data/docking_results.zip
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.109.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 42631 (42K) [application/zip]
Saving to: ‘docking_results.zip.1’

docking_results.zip 100%[===================>]  41.63K  --.-KB/s    in 0.01s   

2025-10-15 08:16:56 (3.33 MB/s) - ‘dock

### Extracting the Scores

gnina stores information docking poses and the score information in the SDF written for the dock.
To analyze and compare the results from all our docking runs (the redocked `Y6J` and all the `Compound_*` ligands), we need to extract this scoring information from the SDF and put it into a structured table.

We can use RDKit PandasTools to read the molecular structures (poses) and their associated properties (scores) from the output SDF. The SDF will contain multiple poses for the docked ligands, and each pose record has the calculated scores (like `minimizedAffinity`, `CNNscore`, `CNNaffinity`, `CNN_VS`, etc.) stored as data fields. The `CNN_VS` score is the product of `CNNscore` and `CNNaffinity`. We would typically want ligands that score highly for both (and thus have a high `CNN_VS` score.

In [ ]:
# uncomment to see file
!cat docking_results/multiple_ligands_results.sdf

cat: docking_results/multiple_ligands_results.sdf: No such file or directory


In [ ]:
from rdkit.Chem import PandasTools
from rdkit.rdBase import BlockLogs
import pandas as pd

score_columns = [
    "minimizedAffinity",
    "CNNscore",
    "CNNaffinity",
    "CNN_VS",
    "CNNaffinity_variance",
]

sdf_paths = [
    "docking_results/multiple_ligands_docked.sdf",
    #"multiple_ligands_docked.sdf",
    "docking_results/Y6J_docked_7LME.sdf",
    #"TJ5_ideal.sdf"
]

df_list = []
for filename in sdf_paths:
    with BlockLogs():
        df_list.append(PandasTools.LoadSDF(filename))

combo_df = pd.concat(df_list)

# PandasTools reads all SDTags as strings, convert score columns to float
for col in score_columns:
    combo_df[col] = combo_df[col].astype(float)

combo_df

ScrubInfo  minimizedAffinity  \
0   {"isomerGroup": 4, "isomerId": 0, "confId": 0,...           -9.14787   
1   {"isomerGroup": 4, "isomerId": 0, "confId": 0,...           -8.05619   
2   {"isomerGroup": 4, "isomerId": 0, "confId": 0,...           -9.34157   
3   {"isomerGroup": 4, "isomerId": 0, "confId": 0,...           -7.62329   
4   {"isomerGroup": 4, "isomerId": 0, "confId": 0,...           -8.09464   
..                                                ...                ...   
4                                                 NaN           -7.49248   
5                                                 NaN           -6.17790   
6                                                 NaN           -6.74170   
7                                                 NaN           -6.82403   
8                                                 NaN           -6.95800   

    CNNscore  CNNaffinity    CNN_VS  CNNaffinity_variance              ID  \
0   0.764619     7.065590  5.402485              0.458909  Compound_12_i0   
1   0.735773     6.955337  5.117549              0.098386  Compound_12_i0   
2   0.615528     6.917795  4.258096              0.597604  Compound_12_i0   
3   0.613069     6.659876  4.082964              0.090788  Compound_12_i0   
4   0.527292     6.999388  3.690723              0.059682  Compound_12_i0   
..       ...          ...       ...                   ...             ...   
4   0.269265     5.728605  1.542512              0.423906             Y6J   
5   0.244571     5.472425  1.338396              0.581873             Y6J   
6   0.212512     5.925318  1.259199              0.615063             Y6J   
7   0.203777     5.810819  1.184113              0.254853             Y6J   
8   0.196746     5.608088  1.103366              0.449305             Y6J   

                                               ROMol  
0   <rdkit.Chem.rdchem.Mol object at 0x7964ad733680>  
1   <rdkit.Chem.rdchem.Mol object at 0x7964ad78c040>  
2   <rdkit.Chem.rdchem.Mol object at 0x7964ad78c270>  
3   <rdkit.Chem.rdchem.Mol object at 0x7964ad78c0b0>  
4   <rdkit.Chem.rdchem.Mol object at 0x7964ad78c890>  
..                                               ...  
4   <rdkit.Chem.rdchem.Mol object at 0x7964ad78e1f0>  
5   <rdkit.Chem.rdchem.Mol object at 0x7964ad78e260>  
6   <rdkit.Chem.rdchem.Mol object at 0x7964ad78e2d0>  
7   <rdkit.Chem.rdchem.Mol object at 0x7964ad78e340>  
8   <rdkit.Chem.rdchem.Mol object at 0x7964ad78e3b0>  

[63 rows x 8 columns]

In [ ]:
#top_poses = combo_df.sort_values(
#    by="minimizedAffinity", ascending=True
#).drop_duplicates("ID")
#top_poses

top_poses = combo_df.sort_values(
    by="minimizedAffinity", ascending=True
)
top_poses

ScrubInfo  minimizedAffinity  \
5   {"isomerGroup": 4, "isomerId": 0, "confId": 0,...           -9.34666   
2   {"isomerGroup": 4, "isomerId": 0, "confId": 0,...           -9.34157   
18  {"isomerGroup": 4, "isomerId": 1, "confId": 0,...           -9.20305   
0   {"isomerGroup": 4, "isomerId": 0, "confId": 0,...           -9.14787   
32  {"isomerGroup": 2, "isomerId": 0, "confId": 0,...           -9.14357   
..                                                ...                ...   
42  {"isomerGroup": 1, "isomerId": 0, "confId": 0,...           -6.73174   
2                                                 NaN           -6.54141   
34  {"isomerGroup": 2, "isomerId": 0, "confId": 0,...           -6.46708   
51  {"isomerGroup": 0, "isomerId": 0, "confId": 0,...           -6.18458   
5                                                 NaN           -6.17790   

    CNNscore  CNNaffinity    CNN_VS  CNNaffinity_variance              ID  \
5   0.454894     6.811048  3.098305              0.465547  Compound_12_i0   
2   0.615528     6.917795  4.258096              0.597604  Compound_12_i0   
18  0.735542     7.275836  5.351683              0.277724  Compound_12_i1   
0   0.764619     7.065590  5.402485              0.458909  Compound_12_i0   
32  0.407603     6.525291  2.659726              0.556016      Compound_1   
..       ...          ...       ...                   ...             ...   
42  0.469921     6.405369  3.010015              0.316577      Compound_4   
2   0.377921     6.075754  2.296158              0.064094             Y6J   
34  0.370558     6.170868  2.286664              0.173717      Compound_1   
51  0.380530     5.935371  2.258587              0.246323     Compound_83   
5   0.244571     5.472425  1.338396              0.581873             Y6J   

                                               ROMol  
5   <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7e340>  
2   <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7e1f0>  
18  <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7e8f0>  
0   <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7e110>  
32  <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7ef10>  
..                                               ...  
42  <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7f370>  
2   <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7fae0>  
34  <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7eff0>  
51  <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7f760>  
5   <rdkit.Chem.rdchem.Mol object at 0x7d9a26d7fc30>  

[63 rows x 8 columns]

In [ ]:
#top_poses.to_csv("multiple_ligands_results.csv")
top_poses.to_excel("multiple_ligands_results.xlsx")

In [ ]:
top_poses.head()
top_poses['minimizedAffinity']
docking_scores = top_poses['minimizedAffinity']
docking_scores.head()

5    -9.34666
2    -9.34157
18   -9.20305
0    -9.14787
32   -9.14357
Name: minimizedAffinity, dtype: float64

In [ ]:
top_poses_top = top_poses[['minimizedAffinity', 'CNNaffinity']][top_poses['minimizedAffinity'] >= -7]
top_poses_top.head()

minimizedAffinity  CNNaffinity
8            -6.95800     5.608088
52           -6.91704     6.508137
30           -6.90586     6.485485
46           -6.86254     6.501461
49           -6.83454     6.210299

Interestingly, the compounds sorted by `minimizedAffinity` (the Vina score) correlates well with the observed `IC50` value from our table.

In [ ]:
ligand_data = pd.read_csv(
    "https://raw.githubusercontent.com/MolSSI-Education/iqb-2025/refs/heads/main/data/US20240293380_examples.csv"
)
ligand_data.sort_values(by="IC50 (nM)")

SMILES  \
0  Fc1cc(Cl)cc(CN(C(=O)Cc2cncc3ccccc23)c2ccc(cc2)...   
1  Clc1cccc(CN(C(=O)Cc2nnc3ccccn23)c2ccc(cc2)-c2c...   
2  CC(C)(C)NC(=O)C(N(C(=O)Cc1cncc2ccccc12)c1ccc(c...   
4  Clc1cccc(CN(C(=O)Cc2cnc3ccccn23)c2ccc(cc2)-c2c...   
3   Fc1cncc(CN(C(=O)Cc2cncc(F)c2)c2ccc(cc2)C2CNC2)c1   

                         Name  IC50 (nM)  cluster  
0  US20240293380, Compound 12       15.0        0  
1   US20240293380, Compound 1      365.0        1  
2  US20240293380, Compound 63     1027.0        2  
4   US20240293380, Compound 4     1146.0        4  
3  US20240293380, Compound 83     5225.0        3

We can also use our visualization function to visualize the docked ligands to look at how they interact with the binding site.

In [ ]:
v = visualize_poses(
    "docking_files/protein_structures/7LME_fixed.pdb",
    #"7BCS_A_fixed.pdb",
    "docking_results/multiple_ligands_docked.sdf",
    #"multiple_ligands_docked.sdf",
    cognate_file="docking_files/ligand_structures/Y6J_corrected_pose.sdf",
    #cognate_file="TJ5_corrected_pose.sdf",
    animate=True,
)  # Change to True to see an animation of all of the poses
v.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

If we would like to visualize poses for only one molecule, we can use the RDKit's PandasTools again to write an SDF for just that compound.

In [ ]:
compound_name = "Compound_12_i0"

compound_df = combo_df[combo_df["ID"] == compound_name]

PandasTools.WriteSDF(
    compound_df,
    f"docking_results/individual_{compound_name}.sdf",  # Output file path
    molColName="ROMol",  # Name of the column with RDKit molecules
    properties=score_columns,  # List of property columns to include
)


cognate = Chem.MolFromMolFile("docking_files/ligand_structures/Y6J_corrected_pose.sdf")
poses = Chem.SDMolSupplier(f"docking_results/individual_{compound_name}.sdf")

for i, pose in enumerate(poses):
    n_match, rmsd = uru.mcs_rmsd(cognate, pose)
    print(f"{n_match}\t{rmsd:.2f}")

17	6.83
17	6.92
17	6.79
17	6.93
17	2.53
17	8.06
17	6.98
17	6.87
17	2.43


In [ ]:
v = visualize_poses(
    "docking_files/protein_structures/7LME_fixed.pdb",
    f"docking_results/individual_{compound_name}.sdf",
    cognate_file=f"docking_results/individual_{compound_name}.sdf",
    animate=False,
)  # Change to True to see an animation of all of the poses
v.show()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

## Flexible docking

In [ ]:
# Flexible docking with known site/residues
!./gnina \
  -r docking_files/protein_structures/7LME.pdbqt \
  -l docking_files/ligand_structures/ligands_to_dock.sdf \
  --autobox_ligand docking_files/ligand_structures/Y6J_corrected_pose.sdf \
  -o docking_results/multiple_ligands_docked_flex.sdf \
  --flexdist_ligand docking_files/ligand_structures/Y6J_corrected_pose.sdf \
  --flexdist 3.59 \
  --cnn_scoring none \
  --seed 0 \
  --exhaustiveness 16

              _             
             (_)            
   __ _ _ __  _ _ __   __ _ 
  / _` | '_ \| | '_ \ / _` |
 | (_| | | | | | | | | (_| |
  \__, |_| |_|_|_| |_|\__,_|
   __/ |                    
  |___/                     

gnina  master:25e64da   Built Apr 23 2025.
gnina is based on smina and AutoDock Vina.
Please cite appropriately.

Recommend running with single model (--cnn fast)
or without cnn scoring (--cnn_scoring=none).

Commandline: ./gnina -r docking_files/protein_structures/7LME.pdbqt -l docking_files/ligand_structures/ligands_to_dock.sdf --autobox_ligand docking_files/ligand_structures/Y6J_corrected_pose.sdf -o docking_results/multiple_ligands_docked_flex.sdf --flexdist_ligand docking_files/ligand_structures/Y6J_corrected_pose.sdf --flexdist 3.59 --cnn_scoring none --seed 0 --exhaustiveness 16
Flexible residues: A:24 A:25 A:41 A:46 A:49 A:140 A:142 A:145 A:163 A:165 A:166 A:189
Using random seed: 0

0%   10   20   30   40   50   60   70   80   90   100%
|----|----|

## Whole protein docking

In [ ]:
# Docking with whole protein
!./gnina \
  -r docking_files/protein_structures/7LME.pdbqt \
  -l docking_files/ligand_structures/ligands_to_dock.sdf \
  --autobox_ligand docking_files/protein_structures/7LME.pdbqt \
  -o docking_results/whole_docked.sdf \
  --cnn_scoring none \
  --seed 0 \
  --exhaustiveness 64

## Free energy perturbation

In [ ]:
ligands = ["Y6J.mol2", "compound_12.mol2"]

pairs = [(ligands[i], ligands[i+1]) for i in range(len(ligands)-1)]

with open("pairs.txt", "w") as f:
    for a, b in pairs:
        f.write(f"{a} {b}\n")

print("pairs.txt created with the following pairs:")
for a, b in pairs:
    print(f"{a} ↔ {b}")

pairs.txt created with the following pairs:
Y6J.mol2 ↔ compound_12.mol2
